# Testing `ipcmagic` with MPI4Py

Points to look at:
 * `%ipcluster start -n 12 --mpi` starts the cluster and it works. On the terminal the following command should look like this:
    ```bash
    > ps -u $USER | grep ip
    1270 pts/8    00:00:01 ipcontroller
    1278 pts/8    00:00:00 ipcontroller
    1279 pts/8    00:00:00 ipcontroller
    1282 pts/8    00:00:00 ipcontroller
    1285 pts/8    00:00:00 ipcontroller
    1334 ?        00:00:01 ipengine
    1335 ?        00:00:01 ipengine
    1336 ?        00:00:00 ipengine
    1337 ?        00:00:00 ipengine
    1338 ?        00:00:00 ipengine
    1339 ?        00:00:00 ipengine
    1340 ?        00:00:00 ipengine
    1341 ?        00:00:00 ipengine
    1342 ?        00:00:00 ipengine
    1343 ?        00:00:00 ipengine
    1344 ?        00:00:00 ipengine
    1345 ?        00:00:00 ipengine
    31037 ?       00:00:00 slurm_script
    ```
 * `%ipcluster stop` stops the cluster. Check with the same command that all the process shown above no longer exist.
 * After stopping the cluster, it can be restarted by running `%ipcluster start -n 12 --mpi` again.
 * Running `%ipcluster start <...>` while the cluster is active, should give `IPCluster is already running`.
 * Running `%ipcluster stop` whould give `IPCluster not running`.
 * Restarting the kernel kills all the process mentioned above.

In [ ]:
import numpy as np
import ipcmagic
import ipyparallel as ipp

In [ ]:
%ipcluster --help

In [ ]:
%ipcluster --version

In [ ]:
# start a cluster of 12 engines
%ipcluster start -n 12 --mpi

In [ ]:
c = ipp.Client()

In [ ]:
c.ids

In [ ]:
%%px
import socket
from mpi4py import MPI

In [ ]:
%%px
print("Hello World from rank %s of %s on nid %s" % (MPI.COMM_WORLD.rank,
                                                    MPI.COMM_WORLD.size,
                                                    socket.gethostname()))

In [ ]:
view = c[:]
view.activate()

Write the file `psum.py` the defines the function `psum`.

In [ ]:
%%bash
echo 'from mpi4py import MPI' > psum.py
echo 'import numpy as np' >> psum.py
echo '' >> psum.py
echo 'def psum(a):' >> psum.py
echo '    locsum = np.sum(a)' >> psum.py
echo "    rcvBuf = np.array(0.0,'d')" >> psum.py
echo '    MPI.COMM_WORLD.Allreduce([locsum, MPI.DOUBLE],' >> psum.py
echo '        [rcvBuf, MPI.DOUBLE],' >> psum.py
echo '        op=MPI.SUM)' >> psum.py
echo '    return rcvBuf' >> psum.py

In [ ]:
# run the contents of the file on each engine:
view.run('psum.py')

In [ ]:
view.scatter('a',np.arange(16,dtype='float'))

In [ ]:
view['a']

In [ ]:
%px totalsum = psum(a)

In [ ]:
view['totalsum']

In [ ]:
# Stop the cluster
%ipcluster stop